In [ ]:
!pip install -q geopandas
!pip install folium pandas
!pip install -q geopy

import pandas as pd

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
crime_df = pd.read_csv('/content/drive/MyDrive/DivaGuard/web_data.csv')
crime_df.drop_duplicates(keep='first', inplace=True)
crime_df.reset_index(drop=True, inplace=True)

pols_df = pd.read_csv('/content/drive/MyDrive/DivaGuard/police_station_data.csv')

crime_df.tail()

Category                                           Location  \
10505         Commenting                  Trains mumbai, Maharashtra, India   
10506         Commenting  Kemps Corner, Malabar Hill, Mumbai, Maharashtr...   
10507  Touching /Groping  New Delhi, Bhavbhuti Marg, Kamla Market, Ajmer...   
10508  Touching /Groping                        Kibera slum, Nairobi, Kenya   
10509  Touching /Groping                        Kibera slum, Nairobi, Kenya   

                                                Incident           Date/Time  
10505   Stalking,touching,commenting,grouping during ...  00:00 Jan 01, 1970  
10506   Looked straight at me and banged into me.Didn...  17:00 Dec 31, 1969  
10507   I was on the escalator and suddenly someone t...  17:00 Dec 31, 1969  
10508   a girl was sent by her father to go buy a pas...  17:00 Dec 31, 1969  
10509   a girl is coming from a poor family and had s...  17:00 Dec 31, 1969

In [ ]:
from geopy.geocoders import Nominatim
from geopy.extra.rate_limiter import RateLimiter
from tqdm import tqdm

geolocator = Nominatim(timeout=10, user_agent="my-app")
geocode = RateLimiter(geolocator.geocode, min_delay_seconds=1)

add = []
lat = []
lon = []
cat = []
inc = []

pols_add = []
pols_lat = []
pols_lon = []
pols_nam = []

for id, row in tqdm(crime_df.iterrows(), total=len(crime_df)):
  loc = row['Location']
  if 'India' not in loc:
    continue
  idx = -5
  while idx < -1:
    addr = ", ".join(loc.split(', ')[idx:])
    coord = geocode(addr)
    if coord is not None:
      add.append(loc)
      lat.append(coord.latitude)
      lon.append(coord.longitude)
      cat.append(row['Category'])
      inc.append(row['Incident'])
      break
    idx+=1

for id, row in tqdm(pols_df.iterrows(), total=len(pols_df)):
  loc = row['Location']
  idx = -5
  while idx < -1:
    addr = ", ".join(loc.split(', ')[idx:])
    coord = geocode(addr)
    if coord is not None:
      pols_add.append(loc)
      pols_lat.append(coord.latitude)
      pols_lon.append(coord.longitude)
      pols_nam.append(row['Name'])
      break
    idx+=1

100%|██████████| 178/178 [07:17<00:00,  2.46s/it]


In [ ]:
new_df = pd.DataFrame(list(zip(add, lat, lon, cat, inc)),
columns=['Address', 'Latitude', 'Longitude', 'Category', 'Incident'])

In [ ]:
new_df.to_csv('crime_data.csv', index=False)

In [ ]:
new_pols_df = pd.DataFrame(list(zip(pols_nam, pols_add, pols_lat, pols_lon)),
columns=['Name', 'Address', 'Latitude', 'Longitude'])
new_pols_df.to_csv('police_station_lat_log_data.csv', index=False)

NameError: name 'pd' is not defined

In [ ]:
import folium

map1 = folium.Map(
    location=[21,78],
    tiles='cartodbpositron',
    zoom_start=5,
)
new_df.apply(lambda row:folium.CircleMarker(location=[row["Latitude"], row["Longitude"]]).add_to(map1), axis=1)
map1